# What if California gave money to everyone, not only vehicle owners?

Last month, Governor Gavin Newsom [proposed an $11 billion package](https://www.gov.ca.gov/2022/03/23/governor-newsom-proposes-11-billion-relief-package-for-californians-facing-higher-gas-prices/) for Californians facing higher gas prices. Newsom reserved $9 billion of this to send each vehicle owner $400 for each registered vehicle, up to two per person.

In this report, we estimate the poverty impact of this policy and compare it against budget-neutral alternatives that include Californians who don't own vehicles.

In [1]:
from openfisca_us import Microsimulation, ACS
from ca_ubi.vehicle_payment import vehicle_subsidy
import numpy as np
from ca_ubi.ubi import create_ubi_reform

def set_non_ca_weights_to_zero(simulation: Microsimulation):
    person_weight = simulation.calc("person_weight").values
    simulation.set_input("person_weight", 2022, np.where(simulation.calc("state_code", map_to="person").values == "CA", person_weight, 0))
    household_weight = simulation.calc("household_weight").values
    simulation.set_input("household_weight", 2022, np.where(simulation.calc("state_code", map_to="household").values == "CA", household_weight, 0))
    spm_unit_weight = simulation.calc("spm_unit_weight").values
    simulation.set_input("spm_unit_weight", 2022, np.where(simulation.calc("person_weight", map_to="spm_unit").values == 6, spm_unit_weight, 0))
    return simulation

baseline = Microsimulation(dataset=ACS, year=2019)
baseline = set_non_ca_weights_to_zero(baseline)
vehicle_payment_simulation = Microsimulation(vehicle_subsidy, dataset=ACS, year=2019)
vehicle_payment_simulation = set_non_ca_weights_to_zero(vehicle_payment_simulation)
cost_of_vehicle_payment = vehicle_payment_simulation.calc("ca_vehicle_payment", map_to="household").sum()
ca_population = baseline.calc("people").sum()
ubi_amount = cost_of_vehicle_payment / ca_population
print(f"Vehicle payment costs ${cost_of_vehicle_payment / 1e9:.1f}bn, CA population == {ca_population / 1e6:.1f} million, UBI amount == ${ubi_amount:.0f}/year")
ubi_simulation = Microsimulation(create_ubi_reform(ubi_amount), dataset=ACS, year=2019)
ubi_simulation = set_non_ca_weights_to_zero(ubi_simulation)

/home/nikhil/policyengine/openfisca-us/openfisca_us/variables/demographic/person/vehicles_owned.py:28: RuntimeWarning: invalid value encountered in remainder
  % num_adults_in_household


Vehicle payment costs $9.6bn, CA population == 38.7 million, UBI amount == $247/year


In [37]:
import pandas as pd
import plotly.express as px
import plotly.io as pio
pio.renderers.default = "notebook_connected" # As per https://github.com/microsoft/vscode-jupyter/issues/4364#issuecomment-817352686
from ubicenter import format_fig
from ubicenter.plotly import BLUE_COLOR_SEQUENCE


def get_poverty_rates(simulation: Microsimulation, label: str, deep_poverty: bool = False) -> pd.DataFrame:
    in_poverty = simulation.calc(f"spm_unit_is_in{'_deep' if deep_poverty else ''}_spm_poverty", map_to="person")
    baseline_in_poverty = baseline.calc(f"spm_unit_is_in{'_deep' if deep_poverty else ''}_spm_poverty", map_to="person")
    group_names = ["Children", "Adults", "Seniors", "All"]
    poverty_rates = []
    for group in ("is_child", "is_wa_adult", "is_senior", "people"):
        poverty_rates.append(in_poverty[simulation.calc(group) > 0].mean() / baseline_in_poverty[baseline.calc(group) > 0].mean() - 1)
    return pd.DataFrame({
        "Group": group_names,
        "Poverty rate": poverty_rates,
        "Label": label,
        "Type": "Poverty" if not deep_poverty else "Deep poverty",
    })

def get_regular_and_deep_poverty_rates(simulation: Microsimulation, label: str) -> pd.DataFrame:
    regular_df = get_poverty_rates(simulation, label, deep_poverty=False)
    deep_df = get_poverty_rates(simulation, label, deep_poverty=True)
    return pd.concat([regular_df, deep_df])

def get_hovercards(poverty_rate_df: pd.DataFrame) -> list:
    hover_cards = []
    for i, row in poverty_rate_df.iterrows():
        poverty_label = "poverty" if row["Type"] == "Poverty" else "deep poverty"
        if row["Label"] == "Baseline":
            hover = f"The current {poverty_label} rate for <b>{row['Group'].lower()}</b> is <b>{row['Poverty rate']:.1%}</b>"
        else:
            baseline_rate = poverty_rate_df.loc[(poverty_rate_df["Label"] == "Baseline") & (poverty_rate_df["Type"] == row["Type"]), "Poverty rate"].iloc[0]
            hover = f"Under the {'vehicle payment' if row['Label'] == 'Vehicle payment' else 'UBI'}, the {poverty_label} rate for <b>{row['Group'].lower()}</b> would fall<br> by {(row['Poverty rate'] - baseline_rate) / baseline_rate:.1%}"    
        hover_cards.append(hover)
    return hover_cards

simulations = [baseline, vehicle_payment_simulation, ubi_simulation]
labels = ["Baseline", "Vehicle payment", "Person payment"]
poverty_rate_df = pd.concat([get_regular_and_deep_poverty_rates(simulation, label) for simulation, label in zip(simulations, labels)])
poverty_rate_df["hover_card"] = get_hovercards(poverty_rate_df)

fig = px.bar(
    poverty_rate_df[(poverty_rate_df.Label != "Baseline") & (poverty_rate_df.Type == "Poverty")], 
    x="Group", 
    y="Poverty rate", 
    color="Label", 
    barmode="group", 
    color_discrete_sequence=BLUE_COLOR_SEQUENCE, 
    custom_data=["hover_card"],
).update_layout(
    title="Changes to poverty rates by age group",
    yaxis_tickformat=".0%",
    legend_title="",
    xaxis_title="",
).update_traces(
    hovertemplate="%{customdata[0]}",
)
format_fig(fig)

/home/nikhil/anaconda3/envs/policyengine/lib/python3.7/site-packages/ipykernel_launcher.py:36: RuntimeWarning:

divide by zero encountered in double_scalars



In [38]:
fig = px.bar(
    poverty_rate_df[(poverty_rate_df.Label != "Baseline") & (poverty_rate_df.Type == "Deep poverty")], 
    x="Group", 
    y="Poverty rate", 
    color="Label", 
    barmode="group", 
    color_discrete_sequence=BLUE_COLOR_SEQUENCE, 
    custom_data=["hover_card"],
).update_layout(
    title="Changes to deep poverty rates by age group",
    yaxis_tickformat=".0%",
    legend_title="",
    xaxis_title="",
).update_traces(
    hovertemplate="%{customdata[0]}",
)
format_fig(fig)

In [42]:
poverty_rate_df

Group  Poverty rate            Label          Type  \
0  Children      0.000000         Baseline       Poverty   
1    Adults      0.000000         Baseline       Poverty   
2   Seniors      0.000000         Baseline       Poverty   
3       All      0.000000         Baseline       Poverty   
0  Children      0.000000         Baseline  Deep poverty   
1    Adults      0.000000         Baseline  Deep poverty   
2   Seniors      0.000000         Baseline  Deep poverty   
3       All      0.000000         Baseline  Deep poverty   
0  Children     -0.036573  Vehicle payment       Poverty   
1    Adults     -0.036163  Vehicle payment       Poverty   
2   Seniors     -0.034378  Vehicle payment       Poverty   
3       All     -0.035991  Vehicle payment       Poverty   
0  Children     -0.058715  Vehicle payment  Deep poverty   
1    Adults     -0.049712  Vehicle payment  Deep poverty   
2   Seniors     -0.065589  Vehicle payment  Deep poverty   
3       All     -0.053769  Vehicle payment  Deep poverty   
0  Children     -0.060565   Person payment       Poverty   
1    Adults     -0.042252   Person payment       Poverty   
2   Seniors     -0.033661   Person payment       Poverty   
3       All     -0.045473   Person payment       Poverty   
0  Children     -0.120360   Person payment  Deep poverty   
1    Adults     -0.059330   Person payment  Deep poverty   
2   Seniors     -0.061770   Person payment  Deep poverty   
3       All     -0.070770   Person payment  Deep poverty   

                                          hover_card  
0  The current poverty rate for <b>children</b> i...  
1  The current poverty rate for <b>adults</b> is ...  
2  The current poverty rate for <b>seniors</b> is...  
3  The current poverty rate for <b>all</b> is <b>...  
0  The current deep poverty rate for <b>children<...  
1  The current deep poverty rate for <b>adults</b...  
2  The current deep poverty rate for <b>seniors</...  
3  The current deep poverty rate for <b>all</b> i...  
0  Under the vehicle payment, the poverty rate fo...  
1  Under the vehicle payment, the poverty rate fo...  
2  Under the vehicle payment, the poverty rate fo...  
3  Under the vehicle payment, the poverty rate fo...  
0  Under the vehicle payment, the deep poverty ra...  
1  Under the vehicle payment, the deep poverty ra...  
2  Under the vehicle payment, the deep poverty ra...  
3  Under the vehicle payment, the deep poverty ra...  
0  Under the UBI, the poverty rate for <b>childre...  
1  Under the UBI, the poverty rate for <b>adults<...  
2  Under the UBI, the poverty rate for <b>seniors...  
3  Under the UBI, the poverty rate for <b>all</b>...  
0  Under the UBI, the deep poverty rate for <b>ch...  
1  Under the UBI, the deep poverty rate for <b>ad...  
2  Under the UBI, the deep poverty rate for <b>se...  
3  Under the UBI, the deep poverty rate for <b>al...

In [43]:
def get_ubi_performance(df: pd.DataFrame) -> pd.Series:
    # This dataframe will have three rows. We should subtract the row with Label "UBI" from the one with Label "Vehicle payment" and return the result
    return df.loc[(df.Label == "Vehicle payment"), "Poverty rate"] / df.loc[(df.Label == "Person payment"), "Poverty rate"] - 1

grouped_df = poverty_rate_df.groupby(["Group", "Type"]).apply(get_ubi_performance).reset_index()
grouped_df["order"] = grouped_df["Group"].map({"Children": 0, "Adults": 1, "Seniors": 2, "All": 3})
grouped_df["order2"] = grouped_df["Type"].map({"Poverty": 0, "Deep poverty": 1})
grouped_df = grouped_df.sort_values(by=["order", "order2"])

fig = px.bar(
    grouped_df,
    x="Group",
    color="Type",
    y="Poverty rate",
    barmode="group",
    color_discrete_sequence=BLUE_COLOR_SEQUENCE,
).update_layout(
    title="Additional poverty changes with a UBI",
    yaxis_tickformat=".0%",
    yaxis_title="Poverty impact of universal payment relative to vehicle payment",
    legend_title="",
    xaxis_title="",
)
format_fig(fig)

In [30]:
df = pd.concat([
    baseline.df(["spm_unit_weight", "spm_unit_net_income", "spm_unit_fips", "people", "vehicles_owned"]),
    vehicle_payment_simulation.df(["ca_vehicle_payment"]),
    ubi_simulation.df(["ca_basic_income"], map_to="spm_unit"),
], axis=1)

df["equiv_income"] = df["spm_unit_net_income"] / (df["people"] ** 0.5)
from microdf import MicroDataFrame
df = df[df.spm_unit_fips == 6].reset_index()
df = MicroDataFrame(df, weights="spm_unit_weight")
df["decile"] = df["equiv_income"].decile_rank()
decile_dfdf = df.groupby("decile").mean()
decile_df = decile_dfdf[["ca_vehicle_payment", "ca_basic_income", "decile"]].rename(columns={"ca_vehicle_payment": "Vehicle payment", "ca_basic_income": "UBI", "decile": "Decile"})
fig = px.bar(
    decile_df, 
    y=["Vehicle payment", "UBI"], 
    x="Decile", 
    barmode="group", 
    color_discrete_sequence=BLUE_COLOR_SEQUENCE
).update_layout(
    title="Change to net income by decile",
    xaxis_title="Equivalised (OECD) income decile",
    yaxis_tickformat="$",
    xaxis_tickvals=list(range(1, 11)),
    legend_title="",
    yaxis_title="Change to SPM unit net income"
)
format_fig(fig)

In [35]:
original_gini = df.spm_unit_net_income.gini()
vehicle_payment_gini = (df.spm_unit_net_income + df.ca_vehicle_payment).gini()
ubi_gini = (df.spm_unit_net_income + df.ca_basic_income).gini()

print(f"Vehicle payment reduces gini by {vehicle_payment_gini / original_gini - 1:.2%}")
print(f"UBI payment reduces gini by {ubi_gini / original_gini - 1:.2%}")

Vehicle payment reduces gini by -0.55%
UBI payment reduces gini by -0.59%


In [60]:
df = baseline.df(["vehicles_owned", "is_adult", "spm_unit_net_income", "spm_unit_fips", "spm_unit_spm_threshold"], map_to="spm_unit")
df = df[df.spm_unit_fips == 6]
df["Vehicles per adult"] = df.vehicles_owned / df.is_adult
df["SPM unit net income"] = df.spm_unit_net_income
fig = px.scatter(df, x="SPM unit net income", y="Vehicles per adult", opacity=0.005, color_discrete_sequence=[LIGHT_BLUE]).update_layout(
    xaxis_range=[0, 500e3],
    title="Vehicles per adult by SPM unit net income",
)
format_fig(fig)

In [64]:
fig = px.line(df.groupby("SPM unit net income")["Vehicles per adult"].mean().rolling(1000).mean()).update_layout(
    title="Vehicles per adult by SPM unit net income",
    xaxis_range=[0, 500e3],
    yaxis_title="Vehicles per adult",
    legend_title="",
)
format_fig(fig)

In [59]:
df["Poverty status"] = np.select([
    df.spm_unit_net_income <= df.spm_unit_spm_threshold / 2,
    df.spm_unit_net_income <= df.spm_unit_spm_threshold,
    df.spm_unit_net_income > df.spm_unit_spm_threshold,
], [
    "In deep poverty",
    "In poverty",
    "Not in poverty",
])
from ubicenter.plotly import BLUE, DARK_BLUE, LIGHT_BLUE
fig = px.bar(df.groupby("Poverty status")["Vehicles per adult"].mean(), color_discrete_sequence=[LIGHT_BLUE])
fig.update_layout(
    title="Average vehicles per adult by poverty status",
    xaxis_title="",
    yaxis_title="Vehicles per adult",
    legend_title="",
)
format_fig(fig)

In [ ]:
total_vehicles = baseline.calc("vehicles_owned").sum()/1e6
total_drivers = (baseline.calc("vehicles_owned") > 0).sum()/1e6

print(f"{total_vehicles:.1f} million vehicles, {total_drivers:.1f} million drivers.")